# Loading Data Using Dask

This user guide notebook demonstrates how to load unstructured grid datasets in UXarray using Dask. 

In [6]:
import uxarray as ux
from dask.distributed import Client, LocalCluster
import xarray as xr

## Dask Setup

In [36]:
cluster = LocalCluster()
client = Client(cluster)
client

<Client: 'tcp://127.0.0.1:40997' processes=16 threads=256, memory=235.00 GiB>

## Data

This notebook uses two datasets to demonstrate Dask functionality.

The first is a 3.75km MPAS Atmopshere Grid paired with a single diagnostic file

The second isis from the Department of Energy (DOE) Energy Exascale Earth System Model (E3SM). The case is set up as follows:  

- Atmosphere-only (AMIP)  
- Present-day control forcing (F2010)  
- 1-degree horizontal resolution (ne30pg2)  
- Sea surface temperatures and sea ice are set as defaults  
- Run ove

Special thanks to Falko Judt (NSF NCAR MMM) and Rachel Tam (UIUC) for sharing the data with us!sears.  


In [37]:
mpas_grid_path = "/glade/campaign/cisl/vast/uxarray/data/dyamond/3.75km/grid.nc"
mpas_data_path = "/glade/campaign/mmm/wmr/fjudt/projects/dyamond_1/3.75km/diag.2016-08-01_00.00.00.nc"

In [38]:
e3sm_grid_path = (
    "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/E3SM_grid/ne30pg2_grd.nc"
)
e3sm_data_pattern = "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/ENSO_ctl_1std/unstructured/*.nc"

## Loading Large Grid Files
. Since UXarray represents every grid format in the UGRID conventions, multiple pre-processing steps are often applied to the original grid data to ensure compliance with our conventions. Most commonly, these steps include:

- Converting from 1-indexed to 0-indexed connectivity variables
- Replacing existing fill values with our standardized `INT_FILL_VALUE`
- Shifting longitude coordinates to the range [-180, 180]

Many of these operations are relatively simple and can be delayed until the variable is needed. By loading the data as Dask arrays instead of directly into memory, we can delay these computations while still creating a `Grid` instance. An added benefit is that only the variables required are computed when accessed, which is useful since grid files often contain additional variables that may not be immediately needed.

Let's examine an extreme case. Below, we have a complete 3.75 km MPAS atmosphere grid that contains a full set of grid variables, including multiple coordinates and connectivity variables.

First, let's try to eagerly load the entire grid into memory without specifying any chunking.


In [39]:
%%time
uxgrid = ux.open_grid(mpas_grid_path)
uxgrid

None
CPU times: user 14.1 s, sys: 1min 32s, total: 1min 46s
Wall time: 1min 39s


<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * face_node_connectivity: (41943042, 6)
  * face_edge_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

This takes over a minute on a node of Derecho. We can observe that our `Grid` contains a large number of variables, many of which we may never end up using.

Compared to using Xarray directly, this represents a significant difference in performance. Note that because UXarray requires all grids to be internally represented using UGRID conventions, loading a `Grid` will always be slower than a pure Xarray approach.


In [40]:
%%time
xrds = xr.open_dataset(mpas_grid_path)

CPU times: user 11 ms, sys: 100 ms, total: 111 ms
Wall time: 105 ms


One workaround is to specify a `chunks` parameter, which uses Dask to load the grid. Since Dask allows computations to be delayed, we can defer these computations until necessary, significantly reducing the time required to open a grid and explore its contents.

Below, we specify `chunks=-1`, which instructs us to load all of our data as Dask arrays, with a single chunk per variable.


In [41]:
%%time
uxgrid = ux.open_grid(mpas_grid_path, chunks=-1)
uxgrid

-1
CPU times: user 742 ms, sys: 557 ms, total: 1.3 s
Wall time: 14.7 s


<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * face_node_connectivity: (41943042, 6)
  * face_edge_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

We can see above that all our variables are loaded as `dask.array` objects. If we inspect the high-level Dask graph for `face_node_connectivity`, we can observe all the computations and steps taken to parse and encode the data according to the UGRID conventions.


In [42]:
uxgrid.face_node_connectivity.data.dask

HighLevelGraph with 17 layers.
<dask.highlevelgraph.HighLevelGraph object at 0x154d444d3230>
 0. original-open_dataset-verticesOnCell-bf7a984439bb267dd3463be0321be53d
 1. open_dataset-verticesOnCell-bf7a984439bb267dd3463be0321be53d
 2. astype-c92bc80ebc54956fcc28078df192a41f
 3. original-open_dataset-nEdgesOnCell-acc252cd4d77eb187160b7314ab2a543
 4. open_dataset-nEdgesOnCell-acc252cd4d77eb187160b7314ab2a543
 5. astype-fbdcb7f49fdae873ba694bac7fc48701
 6. getitem-149ca190fe8db177a5211959d67d7ee1
 7. array-2a2bc8dce6a9b78455d5fb439011f414
 8. greater_equal-2d1a7a47fd227551905b779fce997c1f
 9. invert-9f8a3423432fa8a6c044a6077f651ab6
 10. transpose-27a470fc1f21f1ecf2b93e74b2929b02
 11. where-8d58b872c1ad4b269110802d019c6040
 12. ne-5373f6ebc9c1a1bad77b4422984d3ec4
 13. where-674faff89656f343b9d92ed9352dd276
 14. sub-2e8e6ffdaeb8aca6261d37bc892ec282
 15. ne-0f992b881c4b11dd6dd37e20b682661f
 16. where-220ec0d25750ec28efbf84f9a4cf39bb

If we want to load this variable into memory, we can use the `.load()` or `.compute()` methods:
- `.load()` performs an in-place loading.
- `.compute()` returns a new variable with the data loaded into memory.

For example, to load the `face_node_connectivity` variable into memory, we would do the following:

In [43]:
uxgrid.face_node_connectivity.load()
uxgrid.face_node_connectivity

<xarray.DataArray 'face_node_connectivity' (n_face: 41943042,
                                            n_max_face_nodes: 6)> Size: 2GB
array([[                   2,                    0,                   64,
                          66,                   65,                    1],
       [                  64,                    0,                   16,
                          32,                   48, -9223372036854775808],
       [                   0,                    2,                    3,
                          17,                   18,                   16],
       ...,
       [            83886069,             83886065,             83886066,
                    83886067,             83886071,             83886070],
       [            83886074,             83886068,             83886069,
                    83886070,             83886076,             83886075],
       [            83886076,             83886070,             83886071,
                    83886072,             83886078,             83886077]])
Dimensions without coordinates: n_face, n_max_face_nodes
Attributes:
    cf_role:      face_node_connectivity
    long name:    Maps every face to its corner nodes.
    start_index:  0
    _FillValue:   -9223372036854775808

If you wanted to use ``.compute()`` instead, below is an example on our ``node_lon`` variable. 

Below we showcase how to load the `node_lon` variable into memory using `.compute()`:

In [44]:
uxgrid.node_lon = uxgrid.node_lon.compute()
uxgrid.node_lon

<xarray.DataArray 'node_lon' (n_node: 83886080)> Size: 336MB
array([ 89.98285 ,  89.93793 ,  89.97223 , ..., -20.905151, -20.925049,
       -20.934937], dtype=float32)
Dimensions without coordinates: n_node

Inspecting our `Grid` once again, we can see that after performing these computations, only the `node_lon` and `face_node_connectivity` variables are loaded into memory, while the remaining variables still exist as Dask arrays.


In [35]:
uxgrid

<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * face_node_connectivity: (41943042, 6)
  * face_edge_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

## TODO (UPDATE THIS): Loading Large Datasets

In [15]:
%%time
uxds = ux.open_dataset(mpas_grid_path, mpas_data_path)
uxds

None


<xarray.UxDataset> Size: 17GB
Dimensions:             (time: 1, StrLen: 64, n_face: 41943042, n_node: 83886080)
Coordinates:
  * time                (time) datetime64[ns] 8B 2016-08-01
Dimensions without coordinates: StrLen, n_face, n_node
Data variables: (12/99)
    xtime_old           (time, StrLen) |S1 64B ...
    taux                (time, n_face) float32 168MB ...
    tauy                (time, n_face) float32 168MB ...
    olrtoa              (time, n_face) float32 168MB ...
    cldcvr              (time, n_face) float32 168MB ...
    vert_int_qv         (time, n_face) float32 168MB ...
    ...                  ...
    umeridional_300hPa  (time, n_face) float32 168MB ...
    umeridional_400hPa  (time, n_face) float32 168MB ...
    uzonal_300hPa       (time, n_face) float32 168MB ...
    uzonal_400hPa       (time, n_face) float32 168MB ...
    xtime               (time, StrLen) |S1 64B ...
    zgrid               (n_face) float32 168MB ...

In [16]:
%%time
uxds = ux.open_dataset(mpas_grid_path, mpas_data_path, chunks=-1)
uxds

None
CPU times: user 154 ms, sys: 12.2 s, total: 12.3 s
Wall time: 12.6 s


<xarray.UxDataset> Size: 17GB
Dimensions:             (time: 1, StrLen: 64, n_face: 41943042, n_node: 83886080)
Coordinates:
  * time                (time) datetime64[ns] 8B 2016-08-01
Dimensions without coordinates: StrLen, n_face, n_node
Data variables: (12/99)
    xtime_old           (time, StrLen) |S1 64B dask.array<chunksize=(1, 64), meta=np.ndarray>
    taux                (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    tauy                (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    olrtoa              (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    cldcvr              (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    vert_int_qv         (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    ...                  ...
    umeridional_300hPa  (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    umeridional_400hPa  (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    uzonal_300hPa       (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    uzonal_400hPa       (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    xtime               (time, StrLen) |S1 64B dask.array<chunksize=(1, 64), meta=np.ndarray>
    zgrid               (n_face) float32 168MB dask.array<chunksize=(41943042,), meta=np.ndarray>

In [17]:
uxds.uxgrid

<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_node_connectivity: (41943042, 6)
  * node_face_connectivity: (83886080, 3)
  * face_edge_connectivity: (41943042, 6)
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

## Chunking

Chunks, which are small pieces of the array of interest, can be divided with Dask to be small enough to fit in memory. 

UXarray inherited the chunking feature from Dask, where the chunks of the data can be specified when loading. 

### Loading **Data** with Chunking

The following example demonstrates loading one monthly output from E3SM. By supplying the `chunks` argument, the data loaded will be split in the way as specified in the given dictionary. Typically, chunking the dataarray or dataset is done when loading the data. 

In the following example, the data is split by the vertical levels in the atmosphere `vert`, as specified in the dictionary `{'vert'=4}`.

In [4]:
data_file_monthonly = "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/ENSO_ctl_1std/unstructured/20231220.F2010.ENSO_ctl.lagreg.ne30pg2_EC30to60E2r2.keeling.eam.h0.0006-12.nc"
grid_file = (
    "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/E3SM_grid/ne30pg2_grd.nc"
)
uxds_e3sm_mon = ux.open_dataset(grid_file, data_file_monthonly, chunks={"lev": 4})

None


Now look at one of the data arrays in the loaded dataset. 

By calling one of the variables `Q` - specific humidity, we can look at the data array dimensions. The full data array has 1 point in time, 72 vertical levels, and a total of 21600 faces in the simulation grid, corresponding to the single monthly we loaded and the info shown below: `time: 1, lev: 72, n_face: 21600`. 

The chunk size is also shown in the second line, where they contain 4 vertical levels instead of 72 (see `chunksize=(1,4,21600)`), proving we have successfully chunked the data.

In [3]:
uxds_e3sm_mon.Q

<xarray.UxDataArray 'Q' (time: 1, lev: 72, n_face: 21600)>
dask.array<open_dataset-Q, shape=(1, 72, 21600), dtype=float32, chunksize=(1, 4, 21600), chunktype=numpy.ndarray>
Coordinates:
  * lev      (lev) float64 0.1238 0.1828 0.2699 0.3986 ... 986.2 993.8 998.5
  * time     (time) object 0007-01-01 00:00:00
Dimensions without coordinates: n_face
Attributes:
    mdims:         1
    units:         kg/kg
    long_name:     Specific humidity
    cell_methods:  time: mean

UXarray also supports the same feature when loading multiple files at once with `open_mfdataset` and the same argument `chunks` as shown above. 

Chunk size is important as it can be significant to performance, depending on the algorithm and usage. There are multiple possible configurations for chunking, such as splitting by uniform dimension size or specific chunk shape. Chunking can be done not only with a specified configuration, it can also be done with the [automatic chunking feature in Dask](https://docs.dask.org/en/stable/array-chunks.html#automatic-chunking). 

Special values when specifying chunk size include: `-1` for no chunking, `None` for no change in original chunking (in rechunking), and `auto` for automatic chunking. The default ideal chunk size in Dask is 128MB, which can be verified by calling `dask.config.get('array.chunk-size')`.

More details on the possible configurations and guidelines on deciding chunk size can be found on [Dask's Page about Array Chunks](https://docs.dask.org/en/stable/array-chunks.html).

### Loading **Grid** with Chunking

UXarray aso support chunking on the unstructured grid files. Both chunking on a single array and chunking the full grid with Dask is supported in UXarray. 

The following shows the grid is first loaded and then chunked by calling `.chunk()`. This chunking method is equivalent to that for chunking **data** by defining chunk size with `chunks` argument when calling `open_dataset()`. 

#### Chunk a Single Array

In [4]:
uxgrid = uxds_e3sm_mon.uxgrid
uxgrid.node_lon = uxgrid.node_lon.chunk()
uxgrid.node_lon.data

dask.array<xarray-<this-array>, shape=(21727,), dtype=float64, chunksize=(21727,), chunktype=numpy.ndarray>

## Loading Data with the `parallel` argument

Similar to Xarray, UXarray also supports loading data in parallel. Performance may not be significant due to the chosen dataset for this notebook; and Dask client configuration requires customization depending on the data. Loading data in parallel using Dask can be helpful where the dataset of interest does not fit in memory and/or executions are to be distributed over several CPU cores or machines independently. 

### Loading 6-year monthly data in **Serial**

We first demo loading 72 monthly files in serial and directly into memory. This case does not take any advantage of the [lazy loading](https://www.geeksforgeeks.org/what-is-lazy-loading/) or parallel input/output that is provided by Dask. 

In [5]:
%%time
# Regular Load
data_files = "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/ENSO_ctl_1std/unstructured/*.nc"
uxds_e3sm_basic_load = ux.open_mfdataset(grid_file, data_files, parallel=False)

CPU times: user 19.4 s, sys: 321 ms, total: 19.7 s
Wall time: 25.4 s


Dask will by default chunk each file as a chunk. If to modify chunk sizes, it is recommended to do so at the call for `open_mfdataset`. It will result in inefficient use of memory if the data is first loaded and rechunked. 

### Loading 6-year monthly data in **Parallel**
The following code demonstrates setting up a local cluster with the use of 128 cores (`n_workers`), with 2 jobs (`threads_per_worker`) for each core. Using a local cluster allows multi-process computation on your local machine (e.g. laptop) and provides a diagnostic dashboard for monitoring process performances. 

Details on cluster configuration can be further read [here](https://gateway.dask.org/usage.html#shutdown-the-cluster).  

In [6]:
cluster = LocalCluster(n_workers=128, threads_per_worker=2)
client = Client(cluster)
client

<Client: 'tcp://127.0.0.1:38183' processes=128 threads=256, memory=235.00 GiB>

The difference between loading in **serial** or **parallel** is setting the argument `parallel` to `True` or `False`. Setting `parallel=True` speeds up the loading step by using `dask.delayed`, where the executions are deferred. 

In [7]:
%%time
uxds_e3sm_parallel_load = ux.open_mfdataset(grid_file, data_files, parallel=True)

CPU times: user 13 s, sys: 1.68 s, total: 14.7 s
Wall time: 13.8 s


In [8]:
uxds_e3sm_parallel_load

<xarray.UxDataset>
Dimensions:              (time: 72, n_face: 21600, lev: 72, ilev: 73,
                          cosp_prs: 7, nbnd: 2, cosp_tau: 7, cosp_scol: 10,
                          cosp_ht: 40, cosp_sr: 15, cosp_sza: 5,
                          cosp_htmisr: 16, cosp_tau_modis: 7, cosp_reffice: 6,
                          cosp_reffliq: 6)
Coordinates: (12/13)
  * lev                  (lev) float64 0.1238 0.1828 0.2699 ... 993.8 998.5
  * ilev                 (ilev) float64 0.1 0.1477 0.218 ... 990.5 997.0 1e+03
  * cosp_prs             (cosp_prs) float64 9e+04 7.4e+04 ... 2.45e+04 9e+03
  * cosp_tau             (cosp_tau) float64 0.15 0.8 2.45 6.5 16.2 41.5 100.0
  * cosp_scol            (cosp_scol) int32 1 2 3 4 5 6 7 8 9 10
  * cosp_ht              (cosp_ht) float64 1.896e+04 1.848e+04 ... 720.0 240.0
    ...                   ...
  * cosp_sza             (cosp_sza) float64 0.0 20.0 40.0 60.0 80.0
  * cosp_htmisr          (cosp_htmisr) float64 0.0 250.0 ... 1.6e+04 1.8e+04
  * cosp_tau_modis       (cosp_tau_modis) float64 0.15 0.8 2.45 ... 41.5 100.0
  * cosp_reffice         (cosp_reffice) float64 5e-06 1.5e-05 ... 5e-05 7.5e-05
  * cosp_reffliq         (cosp_reffliq) float64 4e-06 9e-06 ... 1.75e-05 2.5e-05
  * time                 (time) object 0001-02-01 00:00:00 ... 0007-01-01 00:...
Dimensions without coordinates: n_face, nbnd
Data variables: (12/471)
    lat                  (time, n_face) float64 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    lon                  (time, n_face) float64 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    area                 (time, n_face) float64 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    hyam                 (time, lev) float64 dask.array<chunksize=(1, 72), meta=np.ndarray>
    hybm                 (time, lev) float64 dask.array<chunksize=(1, 72), meta=np.ndarray>
    P0                   (time) float64 1e+05 1e+05 1e+05 ... 1e+05 1e+05 1e+05
    ...                   ...
    soa_c1DDF            (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c1SFWET          (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2DDF            (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2SFWET          (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3DDF            (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3SFWET          (time, n_face) float32 dask.array<chunksize=(1, 21600), meta=np.ndarray>

Loading the data in parallel results in a roughly 1.5x speed up. 

After all computations are done, it is of best practice to explicitly clean all dask workers and scheduler up by shutting down the cluster. 

In [9]:
client.shutdown()